In [1]:
from ngsolve import *
from ngsolve.webgui import Draw

In [2]:
from netgen.occ import Box, OCCGeometry, Glue, X

First example a mesh with **one** Identify for periodicity:

In [3]:
box = Box((0,0,0),(1,1,1))
ngmesh = OCCGeometry(box).GenerateMesh(maxh=0.15)

In [4]:
box = Box((0,0,0),(1,1,1))
box.faces.Max(X).Identify(box.faces.Min(X), "leftright")
geom = Glue([box])
ngmesh = OCCGeometry(geom).GenerateMesh(maxh=0.15)
mesh = Mesh(ngmesh)

Second example a mesh with **two** Identify for periodicity:

In [5]:
box2 = Box((0,0,0),(1,1,1))
box3 = Box((0,1,0),(1,1.5,1))
box2.faces.Max(X).Identify(box2.faces.Min(X), "leftright2")
box3.faces.Max(X).Identify(box3.faces.Min(X), "leftright3")
geom = Glue([box2,box3])
ngmesh2 = OCCGeometry(geom).GenerateMesh(maxh=0.15)
mesh2 = Mesh(ngmesh2)

**Now we want to distribute the meshes over a Cluster:**

In [7]:
from ipyparallel import Cluster
numnodes=12
cluster = await Cluster(engines="mpi").start_and_connect(n=numnodes, activate=True)
compnodes = cluster.broadcast_view()

Starting 12 engines with <class 'ipyparallel.cluster.launcher.MPIEngineSetLauncher'>


  0%|          | 0/12 [00:00<?, ?engine/s]

We can distribute the mesh with one Identifications without problem:

In [8]:
ar = compnodes.push({'ngmesh': ngmesh}, block=False)
ar.wait_interactive()

_push:   0%|          | 0/12 [00:00<?, ?tasks/s]

But the mesh with **two** Identifications won't work:

In [9]:
ar = compnodes.push({'ngmesh2': ngmesh2}, block=False)
ar.wait_interactive()

_push:   0%|          | 0/12 [00:00<?, ?tasks/s]

In [10]:
%%px
from ngsolve import *
from ngsolve.webgui import Draw

NoEnginesRegistered: This operation requires engines. Try client.wait_for_engines(n) to wait for engines to register.

In [ ]:
%%px
mesh2 = Mesh(ngmesh2)
mesh2.ne

In [ ]:
%%px --targets 1
plist = []
for pair in mesh2.ngmesh.GetIdentifications():
    plist += list(mesh2.vertices[pair[0].nr-1].point)
    plist += list(mesh2.vertices[pair[1].nr-1].point)
Draw(mesh2, objects=[{"type" : "lines", "position" : plist,
                      "name": "identification", "color": "purple"}]);

In [ ]:
cluster.shutdown()